In [1]:
# Import lib and config notebook with `DataAnalyst package`
from DataAnalyst.utils.libraries import * #load all packages into JN
from DataAnalyst import IPythonConfig


In [9]:
IPythonConfig.config_jedi()
IPythonConfig.set_cwd()
IPythonConfig.set_autoreload()

Working directory: C:\Users\ilias\Desktop\Stress Testing with GANs-Gdrive

In [3]:
IPythonConfig.reset_config()

In [4]:
os.getcwd()

'C:\\Users\\ilias\\Desktop\\Stress Testing with GANs-Gdrive\\Stress Testing with GANs\\IRRBB\\notebooks'

In [5]:
IPythonConfig.config_libs()

In [6]:
pio.templates.default

'ggplot2'

# Sandbox environment for testing WGAN-GP on timeseries data

## Import libraries and configure Jupyter Notebook environment 

In [32]:
# Import lib and config notebook with `DataAnalyst package`
from DataAnalyst.utils.libraries import * #load all packages into JN
from DataAnalyst import IPythonConfig
IPythonConfig.config_jedi()
IPythonConfig.set_cwd()
IPythonConfig.set_autoreload()
IPythonConfig.config_libs()

# Tensorflow
import tensorflow as tf 
import tensorflow.keras as tfk

Working directory: C:\Users\ilias\Desktop\Stress Testing with GANs-Gdrive\Stress Testing with GANs\IRRBB

In [33]:
# Import in-house modules
# -------------------------
from src import d_and_g
from src.utils.nnvis import GANvis
from src.utils.toydata_generator import dataGenerator
from src.utils.parser import Parser

# Test out Discriminator

In [43]:
# Create datasets
N, V, DISTRIBUTION= 10_000, 1, 'Gaussian'
Pr= dataGenerator.generate_data(N, V, DISTRIBUTION, loc= 1) #real dataset
Pg= dataGenerator.generate_data(N, V, DISTRIBUTION, loc= -1) #fake dataset

In [44]:
df = pd.DataFrame(data=np.concatenate((Pr, Pg), axis=1), columns=['Pr', 'Pg'])
fig= px.histogram(df, opacity=0.5, nbins= int(len(df)/10), histnorm='probability density')
fig.show(config= IPythonConfig.plotly_config)

In [45]:
import plotly.figure_factory as ff
fig= ff.create_distplot(hist_data=[Pr.to_numpy().reshape(-1), Pg.to_numpy().reshape(-1)],
                   group_labels=['Pr', 'Pg'], show_hist=True, bin_size= 0.1)
fig.show(config= IPythonConfig.plotly_config)

In [46]:
# Step 2: train discrimator 

# Create dataset 
x= np.concatenate( (Pr.to_numpy().reshape(-1), Pg.to_numpy().reshape(-1)) )
y= np.concatenate( (np.ones(N), np.zeros(N)) )
# train-test-split 
from sklearn.model_selection import train_test_split 
x_train, x_test, y_train, y_test= train_test_split(x,y, test_size=0.33, random_state=0)

# Create model 
D = d_and_g.init_discriminator(V, number_of_output_units=2, output_activation=tfk.activations.sigmoid)

# Compile model 
D.compile(loss= tfk.losses.SparseCategoricalCrossentropy(), metrics= ['accuracy'])

# Train model 
D.fit(x_train, y_train, batch_size=N*2, epochs=10)

Model: "Discriminator"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_layer (InputLayer)    [(None, 1)]               0         
                                                                 
 hidden_layer_1 (Dense)      (None, 64)                128       
                                                                 
 hidden_layer_2 (Dense)      (None, 32)                2080      
                                                                 
 hidden_layer_3 (Dense)      (None, 16)                528       
                                                                 
 output_layer (Dense)        (None, 2)                 34        
                                                                 
Total params: 2,770
Trainable params: 2,770
Non-trainable params: 0
_________________________________________________________________
Epoch 1/10
1/1 [==============================] - 1

In [47]:
# Evaluate model 
D.evaluate(x_test, y_test)

207/207 [==============================] - 0s 1ms/step - loss: 0.4473 - accuracy: 0.8367


[0.4473429024219513, 0.8366666436195374]

In [48]:
GANvis.plot_decision_boundary(x_train, y_train, D)